In [2]:
from qutip import *
import pickle
import numpy as np
import scipy as sc
import matplotlib.pyplot as plt

from numpy import pi, sqrt, sin, cos, arctan, log, exp, convolve
from scipy.constants import h,hbar,k
from matplotlib import cm


#****** to avoid this error  "divide by zero encountered in true_divide" for calculating SNR
np.seterr(divide='ignore', invalid='ignore')

{'divide': 'warn', 'over': 'warn', 'under': 'ignore', 'invalid': 'warn'}

# Constants

In [3]:
params={'hbar':(hbar),
        'E_J/hbar':(2*pi*3.8*1e9),
        'E_c/hbar':(2*pi*2.9*1e9),
        'n_g':(0.51),
        'T_1':(26*1e-6),
        'T_2':(0.08*1e-6),
        'n_q':(0.02),
        'w_m':(2*pi*25*1e6),
        'n_th':(13),
        'gamma_m':(2*pi*94),
        'g_m':(2*pi*22*1e6),
       }
params

{'hbar': 1.0545718176461565e-34,
 'E_J/hbar': 23876104167.28243,
 'E_c/hbar': 18221237390.8208,
 'n_g': 0.51,
 'T_1': 2.6e-05,
 'T_2': 8e-08,
 'n_q': 0.02,
 'w_m': 157079632.67948967,
 'n_th': 13,
 'gamma_m': 590.6194188748811,
 'g_m': 138230076.75795087}

# Normalized Constants 

In [4]:
#******************************** constants ********************************************
wm=1;     #************** wm=2*pi*25*10**6;
EJ=152*wm    #***********EJ=2*pi*3.8*10**9;
Ec=116*wm    #************Ec=2*pi*2.9*10**9
#gm=0.88*wm;
gm = 0.88*wm;
wq = 1.5*wm;
ng = 0.51;

#wq=sqrt(EJ**2+(4*Ec)**2*(1-2*ng)**2);
teta0=arctan(4*Ec*(1-2*ng)/EJ);
teta=(1/2)*arctan(EJ/(4*Ec*(1-2*ng)));
gm_x=gm*cos(teta0);
gm_z=-gm*sin(teta0);
gm_0=gm*(1-2*ng);
delta=wq-wm;
sigma=wq+wm;
#xi_m = gm_x**2*((1/delta) +(1/sigma))

#************** dissipation parameters **************
nth = 0.5;
nq = 0;
#gamma_m = (94/25)*10**(-6);


gamma_a = 0*100 / (26*25*2*pi); #*********** life time or relaxation time T1 = 0.26 micro sec , gamma_a = 1/T1 noraml to wm
gamma_z = 0*100 / (8*25*2*pi); #*********** dephasing or intirinsic decoherence time T2 = 0.08 micro se


print("wq =", wq,"delta =", delta, "sigma=", sigma)

wq = 1.5 delta = 0.5 sigma= 2.5


# Kets & Operators

In [10]:
Hm=10; # dimension of the mechanical Hilbert space

H = wm*a.dag()*a + (wq/2)*sz + gm_x*sx*(a + a.dag()) +  gm_z*sz*(a+a.dag());
#****************** defining nth-list ************************

gamma_m = np.linspace(0,0.01,51)

#*********************************** kets & operators **********************************
a=tensor(identity(2), destroy(Hm))
sz=tensor(sigmaz(),identity(Hm))
sx=tensor(sigmax(),identity(Hm))
sy=tensor(sigmay(),identity(Hm))
sp=tensor(sigmap(),identity(Hm))
sm=tensor(sigmam(),identity(Hm))
#********************************************
XXm = sm*a.dag() - sp*a;
YYm = sm*a - sp*a.dag();

nm = a.dag()*a;
g2 = a.dag()*a.dag()*a*a;
Xm = (a + a.dag())/sqrt(2);
Pm = 1j*(a.dag() - a)/sqrt(2);

coma = a*a.dag() - a.dag()*a;
comq = sm*sp + sp*sm;
    
#********************* Collapce operators ***********************
rho_ss = []
c_ops = []
for i in range(len(gamma_m)):
    c_ops.append(sqrt(gamma_m[i]*(1+nth))*a);
    c_ops.append(sqrt(gamma_m[i]*nth)*a.dag());
    
    c_ops.append(sqrt(gamma_a*(1+nq))*sm);
    c_ops.append(sqrt(gamma_a*nq)*sp);
    c_ops.append(sqrt(gamma_z*(1+nq))*sz);
    c_ops.append(sqrt(gamma_z*nq)*sz);
    rho_ss.append(steadystate(H, c_ops[i]))
#********************** Expectations ****************************
expct_ops = []
expct_ops.append(sz)
expct_ops.append(sp*sm)
expct_ops.append(nm) #******phonon number
expct_ops.append(g2)

TypeError: object of type 'Qobj' has no len()